<a href="https://colab.research.google.com/github/dynamicwebpaige/gemini-and-gemma-examples/blob/main/Satellite_imagery_video_timelapse.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# 🌍 Satellite Timelapse Generator

This notebook generates a timelapse video of any city on Earth for a specific year using NASA's GIBS (Global Imagery Browse Services) satellite data.

It performs the following steps:
1.  **Geocoding:** Converts a City Name to Latitude/Longitude.
2.  **Grid Conversion:** maps those coordinates to NASA's specific "Tile Matrix" (Row/Col).
3.  **Parallel Download:** Fetches daily satellite images concurrently for speed.
4.  **Processing:** Resizes images (to keep file size small) and adds attractive text overlays.
5.  **Rendering:** Stitches the result into an MP4 video.

### 1. Setup and Dependencies
First, we install the necessary libraries for map data (`geopy`), image manipulation (`Pillow`), and computer vision (`opencv-python`).

In [28]:
# Install dependencies
!pip install --quiet opencv-python requests geopy pillow

import os
import math
import cv2
import requests
import shutil
import numpy as np
from datetime import date, timedelta
from concurrent.futures import ThreadPoolExecutor
from geopy.geocoders import Nominatim
from PIL import Image, ImageDraw, ImageFont
from IPython.display import Video

# --- CONFIGURATION ---
ZOOM_LEVEL = 6   # Level 6 is approx 250m resolution.
FPS = 15         # Speed of video
MAX_DIM = 600    # Resizes video to max 600px width/height to ensure <10MB size

### 2. Coordinate Systems & Overlays
NASA stores images in a tile grid. We need a helper function to convert standard Latitude/Longitude into a specific **Row** and **Column** for the GIBS MatrixSet.

We also define a function to draw text using `Pillow` instead of `OpenCV`, as Pillow handles fonts and rendering much more attractively.

In [35]:
def get_tile_coords(lat, lon, zoom):
    """
    Converts Lat/Lon to GIBS MatrixSet Tile Coordinates.
    """
    tile_width_deg = 288.0 / (2 ** zoom)
    col = math.floor((lon + 180) / tile_width_deg)
    row = math.floor((90 - lat) / tile_width_deg)
    return row, col

def get_pixel_coords(lat, lon, row, col, zoom, tile_size=512):
    """
    Calculates pixel (x, y) of a lat/lon within a specific tile.
    """
    tile_width_deg = 288.0 / (2 ** zoom)

    # Tile top-left corner in degrees
    tile_lon_start = (col * tile_width_deg) - 180
    tile_lat_start = 90 - (row * tile_width_deg)

    # Offsets in degrees
    lon_offset = lon - tile_lon_start
    lat_offset = tile_lat_start - lat

    # Convert to pixels
    x = int((lon_offset / tile_width_deg) * tile_size)
    y = int((lat_offset / tile_width_deg) * tile_size)

    return x, y

def add_overlays(cv_img, city_name, date_text, pin_coords=None):
    """
    Adds text with a black outline for readability using PIL.
    """
    # Convert CV2 (BGR) to PIL (RGB)
    img_pil = Image.fromarray(cv2.cvtColor(cv_img, cv2.COLOR_BGR2RGB))
    draw = ImageDraw.Draw(img_pil)

    # Attempt to load a nice bold font, fallback to default if system missing it
    try:
        font = ImageFont.truetype("DejaVuSans-Bold.ttf", 20)
    except IOError:
        font = ImageFont.load_default()

    # Draw Text (Bottom Right: Date)
    bbox = draw.textbbox((0, 0), date_text, font=font)
    text_w, text_h = bbox[2] - bbox[0], bbox[3] - bbox[1]
    w, h = img_pil.size
    draw.text((w - text_w - 10, h - text_h - 10), date_text, font=font, fill=(255, 255, 255), stroke_width=2, stroke_fill=(0,0,0))

    # Draw Pin & City Label
    if pin_coords:
        px, py = pin_coords

        # Draw Pin (Red Circle)
        radius = 5
        draw.ellipse((px - radius, py - radius, px + radius, py + radius), fill=(255, 0, 0), outline=(0, 0, 0))

        # Draw City Name centered above pin
        bbox = draw.textbbox((0, 0), city_name, font=font)
        cw, ch = bbox[2] - bbox[0], bbox[3] - bbox[1]

        cx = px - cw // 2
        cy = py - radius - ch - 5

        # Keep text inside image bounds
        cx = max(5, min(w - cw - 5, cx))
        cy = max(5, min(h - ch - 5, cy))

        draw.text((cx, cy), city_name, font=font, fill=(255, 255, 255), stroke_width=2, stroke_fill=(0,0,0))
    else:
        # Fallback to Top Left if no pin
        draw.text((10, 10), city_name, font=font, fill=(255, 255, 255), stroke_width=2, stroke_fill=(0,0,0))

    # Convert back to BGR for OpenCV
    return cv2.cvtColor(np.array(img_pil), cv2.COLOR_RGB2BGR)

### 3. Downloading Logic
We use `ThreadPoolExecutor` to download images in parallel. Downloading 365 images one by one is slow; doing 10 at a time makes this script run in seconds rather than minutes.

In [30]:
def download_tile(date_str, row, col, folder):
    """
    Downloads a single tile from NASA GIBS.
    """
    url = (f"https://gibs.earthdata.nasa.gov/wmts/epsg4326/best/"
           f"MODIS_Terra_CorrectedReflectance_TrueColor/default/"
           f"{date_str}/250m/{ZOOM_LEVEL}/{row}/{col}.jpg")
    path = os.path.join(folder, f"{date_str}.jpg")

    # Don't re-download if exists
    if os.path.exists(path): return True

    try:
        r = requests.get(url, timeout=5)
        if r.status_code == 200:
            with open(path, 'wb') as f:
                f.write(r.content)
            return True
    except:
        pass
    return False

### 4. Main Execution
Run this cell to start the process. It will ask for your inputs, download the data, and render the video.

In [36]:
# 1. Inputs
city_input = input("Enter City Name (e.g., Paris): ").strip()
year_input = input("Enter Year (e.g., 2024): ").strip()
year = int(year_input)

# 2. Geocode
print(f"Locating {city_input}...")
geolocator = Nominatim(user_agent="sat_timelapse_gen")
loc = geolocator.geocode(city_input)

if loc:
    row, col = get_tile_coords(loc.latitude, loc.longitude, ZOOM_LEVEL)
    print(f"Found: {loc.address}")
    print(f"Grid Coordinates: Lat {loc.latitude:.2f}, Lon {loc.longitude:.2f} -> Tile R{row}/C{col}")

    # Calculate Pin Position (relative to original 512x512 tile)
    raw_pin_x, raw_pin_y = get_pixel_coords(loc.latitude, loc.longitude, row, col, ZOOM_LEVEL)

    # 3. Prepare Folder
    folder = f"imgs_{city_input}_{year}"
    os.makedirs(folder, exist_ok=True)

    # 4. Generate Dates & Download
    start = date(year, 1, 1)
    end = date(year, 12, 31)
    # If current year, only go up to yesterday to avoid 404s
    if year == date.today().year:
        end = date.today() - timedelta(days=1)

    all_dates = [(start + timedelta(days=i)).strftime("%Y-%m-%d") for i in range((end - start).days + 1)]

    print(f"Downloading {len(all_dates)} satellite images...")
    with ThreadPoolExecutor(max_workers=10) as executor:
        executor.map(lambda d: download_tile(d, row, col, folder), all_dates)

    # 5. Stitch Video
    print("Stitching video and applying overlays...")
    images = sorted([img for img in os.listdir(folder) if img.endswith(".jpg")])

    if images:
        # Read first frame to calculate resize ratio
        first_frame = cv2.imread(os.path.join(folder, images[0]))
        h, w, _ = first_frame.shape
        scale = min(MAX_DIM/w, MAX_DIM/h)
        new_w, new_h = int(w * scale), int(h * scale)

        # Scale the pin coordinates to the resized video dimensions
        pin_x = int(raw_pin_x * scale)
        pin_y = int(raw_pin_y * scale)

        video_name = f"{city_input}_{year}.mp4"
        out = cv2.VideoWriter(video_name, cv2.VideoWriter_fourcc(*'mp4v'), FPS, (new_w, new_h))

        for filename in images:
            img = cv2.imread(os.path.join(folder, filename))
            if img is not None:
                # Resize to keep file size small
                img = cv2.resize(img, (new_w, new_h))
                # Add Text and Pin
                img = add_overlays(img, city_input, filename.replace(".jpg", ""), pin_coords=(pin_x, pin_y))
                out.write(img)

        out.release()
        shutil.rmtree(folder) # Cleanup images
        print(f"Success! Video saved: {video_name}")
        print(f"File Size: {os.path.getsize(video_name)/1024/1024:.2f} MB")
    else:
        print("No images were downloaded. Please check the year or internet connection.")
else:
    print("Could not find that city.")

Enter City Name (e.g., Paris): Itasca, TX
Enter Year (e.g., 2024): 2025
Locating Itasca, TX...


Found: Itasca, Hill County, Texas, 76055, United States
Grid Coordinates: Lat 32.16, Lon -97.15 -> Tile R12/C18
Stitching video and applying overlays...
Success! Video saved: Itasca, TX_2025.mp4
File Size: 18.23 MB


### 5. Watch Video
Run this cell to watch the result directly in the notebook.

In [37]:
# define output name
compressed_name = video_name.replace(".mp4", "_compressed.mp4")

print(f"Compressing {video_name}...")

Compressing Itasca, TX_2025.mp4...


In [38]:
# Run ffmpeg:
# -vcodec libx264: Use standard web video codec
# -crf 28: Compression level (higher number = smaller file, lower quality)
!ffmpeg -y -i "$video_name" -vcodec libx264 -crf 28 -preset fast -loglevel error "$compressed_name"

In [39]:
print(f"Original Size: {os.path.getsize(video_name)/1024/1024:.2f} MB")
print(f"Compressed Size: {os.path.getsize(compressed_name)/1024/1024:.2f} MB")

# Now this should display nicely even with embed=True
if os.path.exists(compressed_name):
    display(Video(compressed_name, embed=True))

Original Size: 18.23 MB
Compressed Size: 5.06 MB
